# Covid19 - Brazil (Cities) Basic Graph Analysis
- by Marcelo Rovai
- 02 June 2020

## Main Libraries and setup

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib as mpl
import plotly
import plotly.graph_objs as go
import bar_chart_race as bcr

In [2]:
from cv_util_func import *

In [3]:
import warnings
warnings.filterwarnings("ignore")

In [4]:
pd.set_option('display.float_format', lambda x: '%.f' % x)
pd.options.display.float_format = '{:,}'.format
mpl.rcParams['figure.dpi'] = 150
plt.style.use('seaborn-paper')

## Datasets

### Worldometers Daily Data

- Based on TDS article: [Track Coronavirus in Your Country by Displaying Notifications Using Python](https://towardsdatascience.com/coronavirus-track-coronavirus-in-your-country-by-displaying-notification-c914b5652088)

In [7]:
worldmetersLink = "https://www.worldometers.info/coronavirus/"

In [8]:
data_wd_covid_br, today = get_wordometers_covid('Brazil', worldmetersLink)
# Saving Brazil info
Total_infected = data_wd_covid_br[0]
New_Cases = data_wd_covid_br[1]
Total_Deaths = data_wd_covid_br[2]
New_Deaths = data_wd_covid_br[3] 
Recovred = data_wd_covid_br[4] 
Active_Case = data_wd_covid_br[5] 
Serious_Critical = data_wd_covid_br[6]
date = today


Brazil - Worldometers Daily Data

Today is 2020-06-14 17:49:56.473282 
- Total infected = 867.624 
- New Cases = 16.828 
- Total Deaths = 43.332 
- New Deaths = 541 
- Recovered = 437.512 
- Active Cases = 9.902 
- Serious-Critical = 386.780


### Covid19

Confirmed cases by day, using information from the news. Covid19br dataset is available at GitHub https://github.com/wcota/covid19br, with data by city compiled from original dataset provided by [Brasil.IO](https://brasil.io/dataset/covid19/caso/). <br>
Thanks to: 
- [Wesley Cota](https://wesleycota.com), PhD candidate - Complex Networks/Physics (Universidade Federal de Viçosa - Brazil and Universidad de Zaragoza - Spain) 
- [Alvaro Justen](https://blog.brasil.io/author/alvaro-justen.html) from [Brasil.IO](https://brasil.io/dataset/covid19/caso/).

License: [Creative Commons Attribution-ShareAlike 4.0 International (CC BY-SA 4.0)](https://creativecommons.org/licenses/by-sa/4.0/)

More information: https://wcota.me/covid19br and [ESPECIAL COVID-19 - Dados por Município](https://brasil.io/covid19/)

**Number of total cases by city** 

In [88]:
today = datetime.datetime.today()

In [90]:
dt, dt_tm, dt_tm_city, dt_state, total_cases, deaths, cfr = get_brazil_cv_data(
    today, save=False)


Today is 2020/6/15. Dataset with 4721 observations.


Total number of cases in Brasil at 6/15: 868,380 (43402 fatal) with a CFR of 5.0%


In [91]:
dt_tm.head(2)

date country  state          city   ibgeID  newDeaths  deaths  \
0  2020-02-25  Brazil     SP  São Paulo/SP  3550308          0       0   
1  2020-02-25  Brazil  TOTAL         TOTAL        0          0       0   

   newCases  totalCases  deaths_per_100k_inhabitants  \
0         1           1                          0.0   
1         1           1                          0.0   

   totalCases_per_100k_inhabitants  deaths_by_totalCases _source  
0             0.008159999999999999                   0.0     SES  
1           0.00047999999999999996                   0.0     NaN

## Plot a Resumen Tables

### Worldometer

In [84]:
def plot_wm_table(country, worldmetersLink, show=False, save=True):
    data_wm, today = get_wordometers_covid(country, worldmetersLink)
    wm_date = str(today.year)+'/'+ str(today.month) +'/'+ str(today.day) +' - '+str(today.hour)+'h'
    wm = ['Total_infected', 'New_Cases', 'Total_Deaths', 'New_Deaths', 'Recovered', 'Active_Case' , 'Serious_Critical']

    fig = go.Figure(data=[
        go.Table(header=dict(values=['Wordometers', 'Brazil Data'],
                             fill_color='#D6D6D6',
                             align=['center', 'center'],
                             font=dict(color='green', size=16)),
                 cells=dict(
                     values=[wm, data_wm],
                     fill_color="#E5ECF6",
                     align=['center', 'center'],
                     font=dict(color='firebrick', size=15),
                     height=30))
    ])
    fig.update_layout(
        title='{} Wordometer Data - {}'.format(country, wm_date),
        font=dict(size=16, color="#7f7f7f"),
        margin=dict(l=20, r=20, t=50, b=20),
        autosize=False,
        width=550,
        height=350,
        )

    if save == True:
        fig.write_image('../graphs/wm_table.png')
    if show == True:
        fig.show()

In [66]:
plot_wm_table('Brazil', worldmetersLink, show=True, save=True)


Brazil - Worldometers Daily Data

Today is 2020-06-14 18:53:41.562430 
- Total infected = 867.624 
- New Cases = 16.828 
- Total Deaths = 43.332 
- New Deaths = 541 
- Recovered = 437.512 
- Active Cases = 9.902 
- Serious-Critical = 386.780


### GeoData Table

In [86]:
br_shp, br_cities = load_geodata()

Number of Brazilian Cities: 5,570
Total Brazilian Population: 210,147,125
Total Brazilian Territory : 8,985,590.0 km2 (aprox.)
Average Demografic Density : 23.0 hab/km2 (aprox.)


In [111]:
def get_Brazil_data(dt, br_shp, br_cities):
    total_cases = dt.totalCases.sum()
    deaths = dt.deaths.sum()
    cfr = round((deaths / total_cases) * 100, 2)
    date = datetime.datetime.today()
    cv_city = pd.merge(br_cities, dt, on='COD. IBGE')
    cv_city['TotalCases/1M pop'] = round(
        cv_city.totalCases / (cv_city['POP_2019'] / 1000_000), 1)
    cv_city['Deaths/1M pop'] = round(
        cv_city.deaths / (cv_city['POP_2019'] / 1000_000), 1)
    deaths_city = cv_city.loc[cv_city['deaths'] != 0].copy()
    cv_city_pnt = cv_city.copy()
    cv_city_pnt['geometry'] = cv_city_pnt['geometry'].representative_point()
    deaths_city_pnt = cv_city_pnt[cv_city_pnt.deaths != 0]
    
    number_cities_cases = len(cv_city.index)
    number_cities_deaths = len(deaths_city.index)
    print(
        'Brazil: Total number of Covid19 cases at {}/{}: {:,} ({:,} fatal) in {:,} cities with a CFR of {}%'
        .format(date.month, date.day, total_cases, deaths, number_cities_cases,
                cfr))

    dt_city = cv_city_pnt.sort_values('totalCases', ascending=False).copy()
    dt_city = dt_city[[
        'City', 'UF', 'POP_2019', 'AREA APROX', 'DENS. DEMO', 'totalCases',
        'deaths', 'CFR[%]', 'TotalCases/1M pop', 'Deaths/1M pop'
    ]].reset_index(drop=True)
    dt_city.index += 1
    file = '../data/Covid_Database_Brazil/cv19_Brazil_' + str(
        date.month) + '-' + str(date.day) + '-' + str(date.year) + '.xlsx'
    dt_city.to_excel(file)

    return cv_city, deaths_city, cv_city_pnt, deaths_city_pnt, total_cases, deaths, cfr, number_cities_cases, number_cities_deaths

In [112]:
cv_city, deaths_city, cv_city_pnt, deaths_city_pnt, total_cases, deaths, cfr, number_cities_cases, number_cities_deaths = get_Brazil_data(
    dt, br_shp, br_cities)

Brazil: Total number of Covid19 cases at 6/15: 868,380 (43,402 fatal) in 4,697 cities with a CFR of 5.0%


In [113]:
perc_cases = round((number_cities_cases/5570)*100, 0)
perc_deaths = round((number_cities_deaths/5570)*100, 0)

In [130]:
geo = [
    'Total number of Cases', 'Total number of Deaths', 'CFR [%]',
    'Total number of Brazil cities', 'Number of Identified cities with cases',
    'Brazilian cities with cases [%]',
    'Number of Identified cities with deaths',
    'Brazilian cities with deaths [%]'
]
data_geo = [
    total_cases, deaths, cfr, 5570, number_cities_cases, perc_cases,
    number_cities_deaths, perc_deaths
]

In [131]:
def plot_geo_table(today, geo, data_geo, show=False, save=True):
    
    
    geo_date = str(today.year)+'/'+ str(today.month) +'/'+ str(today.day) +' - '+str(today.hour)+'h'
    wm = ['Total_infected', 'New_Cases', 'Total_Deaths', 'New_Deaths', 'Recovered', 'Active_Case' , 'Serious_Critical']

    fig = go.Figure(data=[
        go.Table(header=dict(values=['Geo Summary', 'Brazil Data'],
                             fill_color='#D6D6D6',
                             align=['center', 'center'],
                             font=dict(color='green', size=16)),
                 cells=dict(
                     values=[geo, data_geo],
                     fill_color="#E5ECF6",
                     align=['right', 'center'],
                     font=dict(color='firebrick', size=15),
                     height=30))
    ])
    fig.update_layout(
        title='Brazil Geo Data summary - {}'.format(geo_date),
        font=dict(size=16, color="#7f7f7f"),
        margin=dict(l=20, r=20, t=50, b=20),
        autosize=False,
        width=700,
        height=350,
        )

    if save == True:
        fig.write_image('../graphs/geo_table.png')
    if show == True:
        fig.show()

In [132]:
plot_geo_table(today, geo, data_geo, show=True, save=True)

### Total cases by state

In [11]:
def plot_table(dx, show=False, save=False):
    date = datetime.datetime.today()
    total_cases = dx.totalCases.sum()
    total_deaths = dx.deaths.sum()

    fig = go.Figure(data=[
        go.Table(header=dict(values=list(dx.columns),
                             fill_color='#D6D6D6',
                             align=['center', 'center'],
                             font=dict(color='green', size=16)),
                 cells=dict(
                     values=[dx.state, dx.deaths, dx.totalCases, dx['CFR[%]']],
                     fill_color="#E5ECF6",
                     align=['center', 'center'],
                     font=dict(color='firebrick', size=15),
                     height=30))
    ])
    fig.update_layout(
        title='Brazil Data by States - {}/{}/{}'.format(
            date.year,
            date.month,
            date.day,
        ),
        font=dict(size=16, color="#7f7f7f"),
        margin=dict(l=20, r=20, t=50, b=20),
        autosize=False,
        width=600,
        height=1000,
        annotations=[
            dict(x=0,
                 y=0.05,
                 text='    Brazil Total      Deaths: {:,}       Cases: {:,}'.
                 format(total_deaths, total_cases),
                 showarrow=False,
                 xref='paper',
                 yref='paper',
                 xanchor='left',
                 yanchor='auto',
                 xshift=0,
                 yshift=0,
                 font=dict(size=16, color="#7f7f7f"))
        ])

    if save == True:
        fig.write_image('../graphs/state_table.png')
    if show == True:
        fig.show()

In [83]:
dx = dt_state.sort_values('deaths', ascending=False)
plot_table(dx, show=True, save=True)

## Timelines

### Timeline Brazil

In [11]:
plot_cases(dt_tm, 'TOTAL', y_scale='linear', n_0=1000, mov=7, show=True, save=False)

In [12]:
plot_cases(dt_tm, 'TOTAL', y_scale='log', n_0=1000, mov=7, show=True, save=False)

### Timeline of cases per city**

In [70]:
top_cities = list(dt.sort_values('totalCases', ascending=False)[:10].city)
top_cities

['São Paulo/SP',
 'Rio de Janeiro/RJ',
 'Fortaleza/CE',
 'Brasília/DF',
 'Manaus/AM',
 'Salvador/BA',
 'Recife/PE',
 'Belém/PA',
 'São Luís/MA',
 'Maceió/AL']

In [74]:
top_cities_deaths = list(dt.sort_values('deaths', ascending=False)[:15].city)
top_cities_deaths

['São Paulo/SP',
 'Rio de Janeiro/RJ',
 'Fortaleza/CE',
 'Belém/PA',
 'Manaus/AM',
 'Recife/PE',
 'Salvador/BA',
 'São Luís/MA',
 'Guarulhos/SP',
 'Maceió/AL',
 'Jaboatão dos Guararapes/PE',
 'Osasco/SP',
 'Duque de Caxias/RJ',
 'Brasília/DF',
 'Ananindeua/PA']

In [14]:
for city in top_cities:
    plot_cases(dt_tm, city, y_scale='linear', n_0=100, mov=7, show=True, save=False)
    plot_cases(dt_tm, city, y_scale='log', n_0=100, mov=7, show=True, save=False) 
    plot_mov_ave_deaths_last_week(dt_tm, city, y_scale='linear', n_0=3, mov=7, show=True, save=False)

### Specific cities analisis 

In [68]:
city = "Duque de Caxias/RJ"
plot_cases(dt_tm, city, y_scale='linear', n_0=100, mov=7, show=True, save=False)
plot_cases(dt_tm, city, y_scale='log', n_0=100, mov=7, show=True, save=False) 
plot_mov_ave_deaths_last_week(dt_tm, city, y_scale='linear', n_0=3, mov=7, show=True, save=False)

## Timeline New Deaths versus Previus Week 

In [15]:
def plot_mov_ave_deaths_last_week_2(data,
                                  city,
                                  n_0=100,
                                  y_scale='log',
                                  mov=7,
                                  graph='bar',
                                  show=False,
                                  save=True,
                                  rect=False,
                                  x0=None,
                                  x1=None,
                                  text=None):
    date = datetime.datetime.today()
    data = data[data.city == city]
    tst = data[data.deaths >= n_0]
    tst.reset_index(drop=True, inplace=True)

    tst['new_deaths'] = tst['deaths'] - tst['deaths'].shift(1)
    tst['new_deaths_Mov_Ave'] = tst.iloc[:, -1].rolling(window=mov).mean()
    tst['mov_ave_new_deaths_last_week'] = tst['new_deaths_Mov_Ave'] - tst[
        'new_deaths_Mov_Ave'].shift(7)
    fig = go.Figure()
    if graph == 'bar':
        fig.add_trace(
            go.Bar(x=tst.date,
                   y=round(tst.new_deaths_Mov_Ave),
                   name='New daily deaths'))
        fig.add_trace(
            go.Bar(x=tst.date,
                   y=round(tst.mov_ave_new_deaths_last_week),
                   name='New daily deaths vs last week'))
    else:
        fig.add_trace(
            go.Scatter(x=tst.date,
                       y=round(tst.new_deaths_Mov_Ave),
                       name='New daily Deaths',
                       line=dict(color='royalblue', width=2)))
        fig.add_trace(
            go.Scatter(x=tst.date,
                       y=round(tst.mov_ave_new_deaths_last_week),
                       name='New daily deaths vs last week',
                       line=dict(color='firebrick', width=2)))
    if rect == True:
        fig.update_layout(
            shapes=[
                # 1st highlight during Feb 4 - Feb 6
                dict(
                    type="rect",
                    # x-reference is assigned to the x-values
                    xref="x",
                    # y-reference is assigned to the plot paper [0,1]
                    yref="paper",
                    x0=x0,
                    y0=0,
                    x1=x1,
                    y1=1,
                    fillcolor="LightSalmon",
                    opacity=0.3,
                    layer="below",
                    line_width=0,
                )
            ],
            annotations=[
                dict(x=x0,
                     y=0.8,
                     xref="x",
                     yref='paper',
                     text=text,
                     showarrow=True,
                     font=dict(family="Courier New, monospace",
                               size=16,
                               color="#ffffff"),
                     align="center",
                     arrowhead=2,
                     arrowsize=1,
                     arrowwidth=2,
                     arrowcolor="#636363",
                     ax=20,
                     ay=-30,
                     bordercolor="#c7c7c7",
                     borderwidth=2,
                     borderpad=4,
                     bgcolor="#ff7f0e",
                     opacity=0.5)
            ])

    fig.update_layout(
        title='Brazil ({}) - New Daily Deaths by Covid-19 versus same day previous week'.
        format(city),
        xaxis_title="Day",
        yaxis_title="Number of Deaths",
        yaxis_type=y_scale,
        font=dict(size=10, color="#7f7f7f"),
        legend=dict(x=0,
                    y=1.0,
                    bgcolor='rgba(255, 255, 255, 0)',
                    bordercolor='rgba(255, 255, 255, 0)'),
        annotations=[
            dict(
                x=0,
                y=1.05,
                text='Deaths over {:,} - Y-scale: {} ({}-day rolling average) - {}/{}/{}'
                .format(n_0, y_scale, mov, date.year, date.month, date.day),
                showarrow=False,
                xref='paper',
                yref='paper',
                xanchor='left',
                yanchor='auto',
                xshift=0,
                yshift=0,
                font=dict(size=10, color="#7f7f7f")),
            dict(
                x=0,
                y=1.05,
                text='Deaths over {:,} - Y-scale: {} ({}-day rolling average) - {}/{}/{}'
                .format(n_0, y_scale, mov, date.year, date.month, date.day),
                showarrow=False,
                xref='paper',
                yref='paper',
                xanchor='left',
                yanchor='auto',
                xshift=0,
                yshift=0,
                font=dict(size=10, color="#7f7f7f")),
            dict(x=1,
                 y=-0.10,
                 text="Source: Brasil.io - https://brasil.io/dataset/covid19/caso/",
                 showarrow=False,
                 xref='paper',
                 yref='paper',
                 xanchor='right',
                 yanchor='auto',
                 xshift=0,
                 yshift=0,
                 font=dict(size=8, color='royalblue')),
            dict(x=1,
                 y=-0.14,
                 text="Created by Marcelo Rovai - https://MJRoBot.org",
                 showarrow=False,
                 xref='paper',
                 yref='paper',
                 xanchor='right',
                 yanchor='auto',
                 xshift=0,
                 yshift=0,
                 font=dict(size=8, color='royalblue'))
        ])

    if save == True:
        city = city.replace('/', '-')
        fig.write_image(
            '../graphs/cv19_' + city + '_' + graph +'_' + y_scale +
            '_CV_Mov_ave_deaths_last_week_Evolution_Graph_updated.png')
    if show == True:
        fig.show()

    return tst

In [16]:
tst = plot_mov_ave_deaths_last_week_2(dt_tm,
                                    'Fortaleza/CE',
                                    y_scale='linear',
                                    n_0=3,
                                    mov=7,
                                    graph='line',
                                    show=True,
                                    save=False,
                                    rect=True, 
                                    x0='2020-05-07',
                                    x1='2020-05-31',
                                    text="Lock-Down")

In [17]:
tst = plot_mov_ave_deaths_last_week_2(dt_tm,
                                    'São Paulo/SP',
                                    y_scale='linear',
                                    n_0=3,
                                    mov=7,
                                    graph='line',
                                    show=True,
                                    save=False,
                                    rect=True, 
                                    x0='2020-05-20',
                                    x1='2020-05-25',
                                    text="Holidays")

In [18]:
tst = plot_mov_ave_deaths_last_week_2(dt_tm,
                                    'Recife/PE',
                                    y_scale='linear',
                                    n_0=3,
                                    mov=7,
                                    graph='line',
                                    show=True,
                                    save=False,
                                    rect=True, 
                                    x0='2020-05-16',
                                    x1='2020-05-31',
                                    text="Lock-Down")

In [19]:
tst = plot_mov_ave_deaths_last_week_2(dt_tm,
                                    'Rio de Janeiro/RJ',
                                    y_scale='linear',
                                    n_0=3,
                                    mov=7,
                                    graph='line',
                                    show=True,
                                    save=False,
                                    rect=False, 
                                    x0='2020-05-07',
                                    x1='2020-05-25',
                                    text="Lock-Down")

In [20]:
tst = plot_mov_ave_deaths_last_week_2(dt_tm,
                                    'Manaus/AM',
                                    y_scale='linear',
                                    n_0=3,
                                    mov=7,
                                    graph='line',
                                    show=True,
                                    save=False,
                                    rect=False, 
                                    x0='2020-05-07',
                                    x1='2020-05-25',
                                    text="Lock-Down")

In [21]:
tst = plot_mov_ave_deaths_last_week_2(dt_tm,
                                    'Porto Velho/RO',
                                    y_scale='linear',
                                    n_0=1,
                                    mov=3,
                                    graph='line',
                                    show=True,
                                    save=False,
                                    rect=False, 
                                    x0='2020-05-07',
                                    x1='2020-05-25',
                                    text="Lock-Down")

In [22]:
plot_cases(dt_tm, 'Porto Velho/RO', y_scale='log', n_0=100, mov=7, show=True, save=False)

In [23]:
tst = plot_mov_ave_deaths_last_week_2(dt_tm,
                                    'TOTAL',
                                    y_scale='linear',
                                    n_0=3,
                                    mov=7,
                                    graph='line',
                                    show=True,
                                    save=False,
                                    rect=False, 
                                    x0='2020-05-07',
                                    x1='2020-05-25',
                                    text="Lock-Down")

In [24]:
tst

date country  state   city  ibgeID  newDeaths  deaths  newCases  \
0   2020-03-18  Brazil  TOTAL  TOTAL       0          3       4       191   
1   2020-03-19  Brazil  TOTAL  TOTAL       0          3       7       138   
2   2020-03-20  Brazil  TOTAL  TOTAL       0          4      11       331   
3   2020-03-21  Brazil  TOTAL  TOTAL       0          7      18       224   
4   2020-03-22  Brazil  TOTAL  TOTAL       0          7      25       396   
..         ...     ...    ...    ...     ...        ...     ...       ...   
81  2020-06-07  Brazil  TOTAL  TOTAL       0        520   36574     19262   
82  2020-06-08  Brazil  TOTAL  TOTAL       0        819   37393     16064   
83  2020-06-09  Brazil  TOTAL  TOTAL       0       1193   38586     31698   
84  2020-06-10  Brazil  TOTAL  TOTAL       0       1238   39824     33790   
85  2020-06-11  Brazil  TOTAL  TOTAL       0       1243   41067     28086   

    totalCases  deaths_per_100k_inhabitants  totalCases_per_100k_inhabitants  \
0          514                       0.0019                          0.24459   
1          643        0.0033299999999999996              0.30598000000000003   
2          974         0.005229999999999999                          0.46348   
3         1198                      0.00857                          0.57008   
4         1594                       0.0119                          0.75852   
..         ...                          ...                              ...   
81      696155                       17.404                        331.27029   
82      712219                     17.79372                        338.91446   
83      743917           18.361420000000003                        353.99818   
84      777707                     18.95053                        370.07739   
85      805793                     19.54202                        383.44231   

    deaths_by_totalCases _source  new_deaths  new_deaths_Mov_Ave  \
0                0.00778     NaN         nan                 nan   
1                0.01089     NaN         3.0                 nan   
2   0.011290000000000001     NaN         4.0                 nan   
3   0.015030000000000002     NaN         7.0                 nan   
4                0.01568     NaN         7.0                 nan   
..                   ...     ...         ...                 ...   
81  0.052539999999999996     NaN       520.0 1,029.5714285714287   
82                0.0525     NaN       819.0 1,040.7142857142858   
83  0.051870000000000006     NaN     1,193.0 1,016.1428571428571   
84  0.051210000000000006     NaN     1,238.0 1,022.4285714285714   
85  0.050960000000000005     NaN     1,243.0   995.4285714285714   

    mov_ave_new_deaths_last_week  
0                            nan  
1                            nan  
2                            nan  
3                            nan  
4                            nan  
..                           ...  
81             99.57142857142867  
82            109.57142857142867  
83            40.571428571428555  
84            27.428571428571445  
85           -33.714285714285666  

[86 rows x 16 columns]

In [25]:
tst[tst.date == '2020-05-08']

date country  state   city  ibgeID  newDeaths  deaths  newCases  \
51  2020-05-08  Brazil  TOTAL  TOTAL       0        754   10027     10407   

    totalCases  deaths_per_100k_inhabitants  totalCases_per_100k_inhabitants  \
51      147096                      4.77142                         69.99667   

    deaths_by_totalCases _source  new_deaths  new_deaths_Mov_Ave  \
51   0.06817000000000001     NaN       754.0   512.5714285714286   

    mov_ave_new_deaths_last_week  
51            124.42857142857139

# Other Graphics

In [26]:
dt_tm.head(2)

date country  state          city   ibgeID  newDeaths  deaths  \
0  2020-02-25  Brazil     SP  São Paulo/SP  3550308          0       0   
1  2020-02-25  Brazil  TOTAL         TOTAL        0          0       0   

   newCases  totalCases  deaths_per_100k_inhabitants  \
0         1           1                          0.0   
1         1           1                          0.0   

   totalCases_per_100k_inhabitants  deaths_by_totalCases _source  
0             0.008159999999999999                   0.0     SES  
1           0.00047999999999999996                   0.0     NaN

In [27]:
dt_tm.columns

Index(['date', 'country', 'state', 'city', 'ibgeID', 'newDeaths', 'deaths',
       'newCases', 'totalCases', 'deaths_per_100k_inhabitants',
       'totalCases_per_100k_inhabitants', 'deaths_by_totalCases', '_source'],
      dtype='object')

In [76]:
def get_dataframe(df, cities, feature, rnd=0, in_data='2020-03-20'):
    data_city = pd.DataFrame(df.date)
    for city in cities:
        df_city = round(df[df.city == city][feature], rnd)
        data_city[city] = df_city
    data_city = data_city.fillna(0)
    data_city = data_city[data_city.date > in_data]
    data_city = data_city.groupby('date').agg(np.sum)
    return data_city

In [29]:
top_cities

['São Paulo/SP',
 'Rio de Janeiro/RJ',
 'Fortaleza/CE',
 'Manaus/AM',
 'Brasília/DF',
 'Salvador/BA',
 'Recife/PE',
 'Belém/PA',
 'São Luís/MA',
 'Maceió/AL']

In [30]:
dead_city = get_dataframe(df=dt_tm,
                          cities=top_cities,
                          feature='deaths_per_100k_inhabitants',
                          rnd=0,
                          in_data='2020-03-20')

In [31]:
bcr.bar_chart_race(dead_city, 
                   title='Brazil Top Cities with COVID-19 cases - Deaths per 100K inhabitants',
                   filename=None)

In [32]:
bcr.bar_chart_race(dead_city, 
                   title='Brazil Top Cities with COVID-19 cases - Deaths per 100K inhabitants',
                  filename='../videos/top_cities_deaths_100K.mp4')

In [33]:
br_capital_cities = ['Belém', 
'Fortaleza',
'Recife',
'Manaus',
'Rio de Janeiro',
'São Luís',
'São Paulo',
'Maceió',
'Rio Branco',
'Vitória',
'Macapá',
'Boa Vista',
'Porto Velho',
'João Pessoa',
'Salvador',
'Natal',
'Teresina',
'Aracaju',
'Brasília',
'Goiânia',
'Porto Alegre',
'Cuiabá',
'Curitiba',
'Palmas',
'Belo Horizonte',
'Florianópolis',
'Campo Grande']

In [34]:
capital_cities = ['Belém/PA', 
'Fortaleza/CE',
'Recife/PE',
'Manaus/AM',
'Rio de Janeiro/RJ',
'São Luís/MA',
'São Paulo/SP',
'Maceió/AL',
'Rio Branco/AC',
'Vitória/ES',
'Macapá/AP',
'Boa Vista/RR',
'Porto Velho/RO',
'João Pessoa/PB',
'Salvador/BA',
'Natal/RN',
'Teresina/PI',
'Aracaju/SE',
'Brasília/DF',
'Goiânia/GO',
'Porto Alegre/RS',
'Cuiabá/MT',
'Curitiba/PR',
'Palmas/TO',
'Belo Horizonte/MG',
'Florianópolis/SC',
'Campo Grande/MS']

In [35]:
dead_capital = get_dataframe(df=dt_tm,
                          cities=capital_cities,
                          feature='deaths_per_100k_inhabitants',
                          rnd=0,
                          in_data='2020-03-20')

In [36]:
dead_capital

Belém/PA  Fortaleza/CE  Recife/PE  Manaus/AM  Rio de Janeiro/RJ  \
date                                                                          
2020-03-21       0.0           0.0        0.0        0.0                0.0   
2020-03-22       0.0           0.0        0.0        0.0                0.0   
2020-03-23       0.0           0.0        0.0        0.0                0.0   
2020-03-24       0.0           0.0        0.0        0.0                0.0   
2020-03-25       0.0           0.0        0.0        0.0                0.0   
...              ...           ...        ...        ...                ...   
2020-06-07     106.0          92.0       75.0       67.0               66.0   
2020-06-08     109.0          96.0       77.0       68.0               67.0   
2020-06-09     110.0          99.0       80.0       69.0               68.0   
2020-06-10     111.0         102.0       83.0       70.0               70.0   
2020-06-11     112.0         105.0       83.0       71.0               72.0   

            São Luís/MA  São Paulo/SP  Maceió/AL  Rio Branco/AC  Vitória/ES  \
date                                                                          
2020-03-21          0.0           0.0        0.0            0.0         0.0   
2020-03-22          0.0           0.0        0.0            0.0         0.0   
2020-03-23          0.0           0.0        0.0            0.0         0.0   
2020-03-24          0.0           0.0        0.0            0.0         0.0   
2020-03-25          0.0           0.0        0.0            0.0         0.0   
...                 ...           ...        ...            ...         ...   
2020-06-07         52.0          40.0       38.0           37.0        35.0   
2020-06-08         52.0          40.0       38.0           37.0        37.0   
2020-06-09         53.0          41.0       40.0           39.0        38.0   
2020-06-10         53.0          43.0       41.0           42.0        41.0   
2020-06-11         54.0          44.0       42.0           44.0        43.0   

            ...  Aracaju/SE  Brasília/DF  Goiânia/GO  Porto Alegre/RS  \
date        ...                                                         
2020-03-21  ...         0.0          0.0         0.0              0.0   
2020-03-22  ...         0.0          0.0         0.0              0.0   
2020-03-23  ...         0.0          0.0         0.0              0.0   
2020-03-24  ...         0.0          0.0         0.0              0.0   
2020-03-25  ...         0.0          0.0         0.0              0.0   
...         ...         ...          ...         ...              ...   
2020-06-07  ...        15.0          7.0         5.0              3.0   
2020-06-08  ...        16.0          7.0         5.0              3.0   
2020-06-09  ...        17.0          8.0         5.0              3.0   
2020-06-10  ...        18.0          8.0         5.0              3.0   
2020-06-11  ...        19.0          9.0         5.0              3.0   

            Cuiabá/MT  Curitiba/PR  Palmas/TO  Belo Horizonte/MG  \
date                                                               
2020-03-21        0.0          0.0        0.0                0.0   
2020-03-22        0.0          0.0        0.0                0.0   
2020-03-23        0.0          0.0        0.0                0.0   
2020-03-24        0.0          0.0        0.0                0.0   
2020-03-25        0.0          0.0        0.0                0.0   
...               ...          ...        ...                ...   
2020-06-07        4.0          3.0        3.0                2.0   
2020-06-08        5.0          3.0        3.0                2.0   
2020-06-09        6.0          3.0        3.0                2.0   
2020-06-10        7.0          3.0        3.0                2.0   
2020-06-11        7.0          3.0        3.0                3.0   

            Florianópolis/SC  Campo Grande/MS  
date                                           
2020-03-21               

In [37]:
bcr.bar_chart_race(dead_capital, 
                   title='Brazil Capital Cities - COVID-19 - Deaths per 100K inhabitants',
                   filename=None)

In [38]:
bcr.bar_chart_race(dead_capital, 
                   title='Brazil Capital Cities - COVID-19 - Deaths per 100K inhabitants',
                  filename='../videos/capital_cities_deaths_100K.mp4')

In [77]:
top_cities_deaths

['São Paulo/SP',
 'Rio de Janeiro/RJ',
 'Fortaleza/CE',
 'Belém/PA',
 'Manaus/AM',
 'Recife/PE',
 'Salvador/BA',
 'São Luís/MA',
 'Guarulhos/SP',
 'Maceió/AL',
 'Jaboatão dos Guararapes/PE',
 'Osasco/SP',
 'Duque de Caxias/RJ',
 'Brasília/DF',
 'Ananindeua/PA']

In [80]:
dead_top_city = get_dataframe(df=dt_tm,
                          cities=top_cities_deaths,
                          feature='deaths_per_100k_inhabitants',
                          rnd=0,
                          in_data='2020-03-20')

In [81]:
bcr.bar_chart_race(dead_top_city, 
                   title='Brazil Top Cities - COVID-19 - Deaths per 100K inhabitants',
                   filename=None)

In [82]:
bcr.bar_chart_race(dead_top_city, 
                   title='Brazil Top Cities - COVID-19 - Deaths per 100K inhabitants',
                  filename='../videos/top_death_cities_deaths_100K.mp4')